<a href="https://colab.research.google.com/github/AaravWattal/RRAM-Models/blob/main/UncleanConductanceAnalysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Imports and Datasets

In [ ]:
from datascience import *
import pandas as pd
import math
import random
import numpy as np
from sklearn.neural_network import MLPRegressor
from sklearn.datasets import make_regression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

from time import time
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import QuantileTransformer
from sklearn.neural_network import MLPRegressor

/usr/local/lib/python3.7/dist-packages/datascience/tables.py:17: MatplotlibDeprecationWarning: The 'warn' parameter of use() is deprecated since Matplotlib 3.1 and will be removed in 3.3.  If any parameter follows 'warn', they should be pass as keyword, not positionally.
  matplotlib.use('agg', warn=False)
/usr/local/lib/python3.7/dist-packages/datascience/util.py:10: MatplotlibDeprecationWarning: The 'warn' parameter of use() is deprecated since Matplotlib 3.1 and will be removed in 3.3.  If any parameter follows 'warn', they should be pass as keyword, not positionally.
  matplotlib.use('agg', warn=False)


In [ ]:
# get file set_sweep for conductange range data
names = ["addr", "pw", "vwl", "vbsl", "preread", "postread"]
data = pd.read_csv("/content/set_sweep.csv", names=names)
data.head(20)

addr            pw  vwl  vbsl        preread       postread
0      0  2.000000e-08  0.5   0.5  151240.470700  115068.986900
1      2  2.000000e-08  0.5   1.0  123855.302200  124977.565700
2      4  2.000000e-08  0.5   1.5  127236.989700  106676.196700
3      6  2.000000e-08  0.5   2.0   93031.982770  133852.645200
4      8  2.000000e-08  0.5   2.5   75606.517090   57549.247700
5     10  2.000000e-08  0.5   3.0   97572.302250   92171.401490
6     12  2.000000e-08  0.6   0.5   46314.963040   50373.876070
7     14  2.000000e-08  0.6   1.0  100303.315400  149505.440600
8     16  2.000000e-08  0.6   1.5  212694.720700   75614.854910
9     18  2.000000e-08  0.6   2.0    5747.716015    5608.268993
10    20  2.000000e-08  0.6   2.5   99390.597620   68173.473680
11    22  2.000000e-08  0.6   3.0  115261.443600   41095.737690
12    24  2.000000e-08  0.7   0.5  138166.881800  131530.809600
13    26  2.000000e-08  0.7   1.0   84032.373080   68859.159200
14    28  2.000000e-08  0.7   1.5   77354.814580   35775.406770
15    30  2.000000e-08  0.7   2.0  156872.819900   48530.561620
16    32  2.000000e-08  0.7   2.5  125683.593900   55771.120680
17    34  2.000000e-08  0.7   3.0    5568.287628    5506.209298
18    36  2.000000e-08  0.8   0.5  102392.493600  150220.804000
19    38  2.000000e-08  0.8   1.0  132950.036700  154280.498200

#Data Splitting and Organizing + Scaled Inputs and Outputs

In [ ]:
x1 = data[['pw']]
x2 = data[['vwl']]
x3 = data[['vbsl']]
x4 = data[['preread']]
y = data[['postread']]

In [ ]:
#y1 is postread conductance
y1 = [1/i for i in y["postread"]]
y1

[8.690438900527072e-06,
 8.001436052934739e-06,
 9.374162474242016e-06,
 7.470902039371875e-06,
 1.7376421759897305e-05,
 1.0849352226769531e-05,
 1.9851559538725805e-05,
 6.688719794990524e-06,
 1.3224914617507928e-05,
 0.00017830813772452017,
 1.4668461881433647e-05,
 2.4333423761446047e-05,
 7.6027814550911116e-06,
 1.4522396317612895e-05,
 2.7952162960130612e-05,
 2.060557237787845e-05,
 1.7930426855464077e-05,
 0.0001816131472450977,
 6.656867580072331e-06,
 6.481700614575796e-06,
 1.4721051287884775e-05,
 7.442452831745275e-05,
 5.634049594621878e-05,
 0.0001722322101690275,
 1.3970482539451259e-05,
 6.374590580047321e-06,
 5.273836525475831e-06,
 6.986837390839469e-05,
 9.174657297741507e-05,
 0.00010813264872506114,
 1.26504756670377e-05,
 1.2281803425473651e-05,
 7.053585453870362e-05,
 9.215173536291485e-05,
 0.0001087810385494796,
 9.763299771001023e-05,
 2.0346814757800057e-05,
 8.587417461918987e-06,
 9.552214151562855e-05,
 0.00010162010169140851,
 0.00010013478119519222,

In [ ]:
#find min and max postread conductance value
print("Min: " + str(min(y1)))
print("Max: " + str(max(y1)))

Min: 4.729955672681199e-07
Max: 0.00019584016408811259


In [ ]:
#I will take the max conductance value and map it to 1 by multiplying by 0.511*10^4
value = 0.511*10**4
print(0.00019584*value)

y3 = [i*value for i in y1]
print(y3)
print(max(y3))
print(min(y3))

1.0007424
[0.04440814278169334, 0.04088733823049652, 0.0479019702433767, 0.03817630942119028, 0.08879351519307523, 0.055440189878792304, 0.10144146924288887, 0.03417935815240158, 0.0675793136954655, 0.9111545837722981, 0.07495584021412594, 0.1243437954209893, 0.03885021323551558, 0.07420944518300189, 0.14283555272626744, 0.10529447485095887, 0.09162448123142143, 0.9280431824224492, 0.03401659333416961, 0.03312149014048232, 0.0752245720810912, 0.38030933970218356, 0.28789993428517796, 0.8801065939637305, 0.07138916577659593, 0.03257415786404181, 0.0269493046451815, 0.35702739067189687, 0.468824987914591, 0.5525578349850624, 0.06464393065856265, 0.06276001550417036, 0.3604382166927755, 0.4708953677044949, 0.5558711069878407, 0.4989046182981523, 0.10397222341235829, 0.04388170323040603, 0.48811814314486185, 0.5192787196430975, 0.5116887319074322, 0.5486938406903997, 0.06573144276053425, 0.33055420906285843, 0.4765589671627595, 0.46629303266009114, 0.5958163938054075, 0.6640364883086296, 0

###Now the inputs must be scaled one by one to 0-1.

####Pulse Width Scaling

In [ ]:
print(x1.index)
print((data.loc[data['pw'] == 2.000000e-08]))

RangeIndex(start=0, stop=32768, step=1)
        addr            pw  vwl  vbsl       preread      postread
0          0  2.000000e-08  0.5   0.5  151240.47070  115068.98690
1          2  2.000000e-08  0.5   1.0  123855.30220  124977.56570
2          4  2.000000e-08  0.5   1.5  127236.98970  106676.19670
3          6  2.000000e-08  0.5   2.0   93031.98277  133852.64520
4          8  2.000000e-08  0.5   2.5   75606.51709   57549.24770
...      ...           ...  ...   ...           ...           ...
32763  65526  2.000000e-08  0.5   2.0  109317.71090   94101.45234
32764  65528  2.000000e-08  0.5   2.5  113645.69790  111313.86480
32765  65530  2.000000e-08  0.5   3.0   94127.21389   71467.48327
32766  65532  2.000000e-08  0.6   0.5   64914.01743   76972.83889
32767  65534  2.000000e-08  0.6   1.0   87013.20735  122600.15050

[4688 rows x 6 columns]


In [ ]:
for element in x1['pw']:
  print(element)

Streaming output truncated to the last 5000 lines.
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
2e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4e-08
4

In [ ]:
#find min and max pulse width value
print(x1.iat[0,0])
print("Min: " + str(min(x1['pw'])))
print("Max: " + str(max(x1['pw'])))

#scale by mapping max pulse width to 1, multiply by 500000
value = 500000
print(2e-06*value)
x1a = [i*value for i in x1['pw']]
print(x1a)

2e-08
Min: 2e-08
Max: 2e-06
1.0
[0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0

####Wordline Voltage Scaling

In [ ]:
for element in x2['vwl']:
  print(element)

Streaming output truncated to the last 5000 lines.
1.3
1.3
1.3
1.3
1.3
1.3
1.4
1.4
1.4
1.4
1.4
1.4
1.5
1.5
1.5
1.5
1.5
1.5
1.6
1.6
1.6
1.6
1.6
1.6
1.7
1.7
1.7
1.7
1.7
1.7
1.8
1.8
1.8
1.8
1.8
1.8
1.9
1.9
1.9
1.9
1.9
1.9
2.0
2.0
2.0
2.0
2.0
2.0
2.1
2.1
2.1
2.1
2.1
2.1
2.2
2.2
2.2
2.2
2.2
2.2
2.3
2.3
2.3
2.3
2.3
2.3
2.4
2.4
2.4
2.4
2.4
2.4
2.5
2.5
2.5
2.5
2.5
2.5
2.6
2.6
2.6
2.6
2.6
2.6
2.7
2.7
2.7
2.7
2.7
2.7
2.8
2.8
2.8
2.8
2.8
2.8
2.9
2.9
2.9
2.9
2.9
2.9
3.0
3.0
3.0
3.0
3.0
3.0
3.1
3.1
3.1
3.1
3.1
3.1
3.2
3.2
3.2
3.2
3.2
3.2
3.3
3.3
3.3
3.3
3.3
3.3
3.4
3.4
3.4
3.4
3.4
3.4
0.5
0.5
0.5
0.5
0.5
0.5
0.6
0.6
0.6
0.6
0.6
0.6
0.7
0.7
0.7
0.7
0.7
0.7
0.799999999999999
0.799999999999999
0.799999999999999
0.799999999999999
0.799999999999999
0.799999999999999
0.899999999999999
0.899999999999999
0.899999999999999
0.899999999999999
0.899999999999999
0.899999999999999
0.999999999999999
0.999999999999999
0.999999999999999
0.999999999999999
0.999999999999999
0.999999999999999
1.1
1.1
1.1
1.1
1.1
1.1
1

In [ ]:
#find min and max vwl value
print(x2.iat[0,0])
print("Min: " + str(min(x2['vwl'])))
print("Max: " + str(max(x2['vwl'])))

#scale by mapping max vwl to 1, multiply by 0.2941176
value = 0.2941176
print(3.4*value)
x2a = [i*value for i in x2['vwl']]
print(x2a)

0.5
Min: 0.5
Max: 3.4
0.9999998399999999
[0.1470588, 0.1470588, 0.1470588, 0.1470588, 0.1470588, 0.1470588, 0.17647055999999997, 0.17647055999999997, 0.17647055999999997, 0.17647055999999997, 0.17647055999999997, 0.17647055999999997, 0.20588231999999998, 0.20588231999999998, 0.20588231999999998, 0.20588231999999998, 0.20588231999999998, 0.20588231999999998, 0.2352940799999997, 0.2352940799999997, 0.2352940799999997, 0.2352940799999997, 0.2352940799999997, 0.2352940799999997, 0.2647058399999997, 0.2647058399999997, 0.2647058399999997, 0.2647058399999997, 0.2647058399999997, 0.2647058399999997, 0.2941175999999997, 0.2941175999999997, 0.2941175999999997, 0.2941175999999997, 0.2941175999999997, 0.2941175999999997, 0.32352936, 0.32352936, 0.32352936, 0.32352936, 0.32352936, 0.32352936, 0.35294111999999994, 0.35294111999999994, 0.35294111999999994, 0.35294111999999994, 0.35294111999999994, 0.35294111999999994, 0.38235288, 0.38235288, 0.38235288, 0.38235288, 0.38235288, 0.38235288, 0.41176463

In [ ]:
print(min(x2a))
print(max(x2a))

0.1470588
0.9999998399999999


####Bitline Voltage Scaling

In [ ]:
for element in x3['vbsl']:
  print(element)

Streaming output truncated to the last 5000 lines.
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2.0
2.5
3.0
0.5
1.0
1.5
2

In [ ]:
#find min and max vbsl value
print(x3.iat[0,0])
print("Min: " + str(min(x3['vbsl'])))
print("Max: " + str(max(x3['vbsl'])))

#scale by mapping max vbsl to 1, multiply by 0.33333
value = 1/3
print(3*value)
x3a = [i*value for i in x3['vbsl']]
print(x3a)

0.5
Min: 0.5
Max: 3.0
1.0
[0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.6666666666666666, 0.8333333333333333, 1.0, 0.16666666666666666, 0.3333333333333333, 0.5, 0.666666666666666

In [ ]:
print(min(x3a))
print(max(x3a))

0.16666666666666666
1.0


####Preread Resistance/Conductance Scaling

In [ ]:
for element in x4['preread']:
  print(element)

Streaming output truncated to the last 5000 lines.
113645.6979
33653.06286
93145.41153
141104.0647
6313.379053
109075.3483
52836.13925
39219.29434
63303.61429
129433.3672
66048.38501
70243.57953
85369.463
25842.33311
94114.33136
108184.4291
91302.24187
205556.8619
18194.31997
56529.03882
99606.40984
10213.0048
7636.240631
72373.38944
98241.09618
110652.318
49948.72011
41759.47112
91643.05609
27810.0175
5733.738683
68866.08514
120332.1072
128230.4048
120437.2115
90795.71859
20155.05676
121906.5411
55557.60846
82201.29358
207965.7417
137588.5148
8037.348737
85465.06939
132059.4697
107626.5098
114267.6048
122447.753
88583.81549
46990.82624
69459.88534
125660.6949
106100.8999
94295.00627
96140.42105
60065.37986
95966.04232
5574.176054
29483.16131
60150.00747
96046.4466
138582.9749
8194.067197
111170.1616
67130.44181
113439.8899
66259.45336
142413.8684
120774.7769
43770.69751
108133.4715
178414.2646
130807.6463
99664.11727
137890.8662
32160.15626
26205.90017
87101.46399
46828.91307
76637.38

In [ ]:
#preread resistance to preread conductance
x5 = [1/i for i in x4["preread"]]

#find min and max preread conductance value
print("Min: " + str(min(x5)))
print("Max: " + str(max(x5)))

#scale by mapping max preread conductance to 1, multiply by 5190.251624
value = 5190.251624
print(2.702846255980851e-07*value)
x5a = [i*value for i in x5]
print(x5a)

Min: 2.702846255980851e-07
Max: 0.00019266888629752488
0.0014028452169526932
[0.03431787536746935, 0.0419057685202596, 0.040792002673417545, 0.05578997103428069, 0.06864820419940337, 0.053193903436874176, 0.11206425058608878, 0.051745563975645024, 0.024402352850688317, 0.9030111457237681, 0.052220750737850326, 0.04503025002890039, 0.03756509198429345, 0.061764905997106705, 0.0670966849598258, 0.03308572911042571, 0.04129617448821218, 0.9321091097918408, 0.050689766813140684, 0.03903911388690877, 0.051451425029408325, 0.03141834368221965, 0.05028259472042638, 0.8920189128175338, 0.07544311656360803, 0.05629576873173315, 0.040430838545868625, 0.07763444281700345, 0.051692768438176794, 0.059732115804074636, 0.06584071056366093, 0.032732674201760285, 0.02915856387354128, 0.058916226182580855, 0.05837993204966318, 0.05775307483666812, 0.11081906255861602, 0.06345831452609434, 0.07358622252453771, 0.05137600777109673, 0.05001116639318968, 0.05582771524428817, 0.04067913586220262, 0.070821197

In [ ]:
print(min(x5a))
print(max(x5a))

0.0014028452169526932
0.9999999999999999


####Postread Resistance/Conductance Scaling

In [ ]:
for element in y1:
  print(element)

Streaming output truncated to the last 5000 lines.
8.144995104703186e-06
6.27578036838965e-05
0.00010435303132141929
0.00010419044201386785
0.0001585845739630273
0.00012628559494950737
1.652409488672912e-05
5.515156215134217e-05
0.00010412927705392931
0.00013314067792028235
0.00012039253396256649
0.00013936176882338525
9.384327898762066e-06
7.181627636719236e-05
0.00010087073304330344
0.00012882613782315818
0.0001313022231302769
0.00014031421154358815
5.383757618675194e-05
1.7122982673968032e-05
0.00013083364135944533
0.00010567893610623298
0.00012660032192747696
0.00014533255894875197
1.3414530837440464e-05
9.246378360724393e-06
0.00010429668532645546
0.00013888423132903336
0.000143950495670982
0.00014938601799105919
0.00017247583872903068
2.6105480364504628e-05
0.00010232508335394383
0.0001416709792682242
0.00015090770925243178
0.00015786590095693168
5.1470733806640086e-05
6.7147815457457345e-06
0.00011069321736629848
0.000150096743587762
0.00012682283544129735
0.00015877028915562284

In [ ]:
#find min and max postread conductance value (y1 is conductance)
print("Min: " + str(min(y1)))
print("Max: " + str(max(y1)))

#scale by mapping max preread conductance to 1, multiply by 5106.204872
value = 5106.204872
print(0.00019584016408811259*value)
y1a = [i*value for i in y1]
print(y1a)

Min: 4.729955672681199e-07
Max: 0.00019584016408811259
1.0
[0.04437516145368966, 0.04085697175649182, 0.04786639409689416, 0.038147956391675404, 0.08872756944831443, 0.05539901519837463, 0.10136613003343978, 0.03415397360462346, 0.067529123451703, 0.9104778815661919, 0.07490017152372277, 0.12425144696313638, 0.03882135970673749, 0.07415433083010983, 0.14272947068995687, 0.10521627406627156, 0.09155643296641032, 0.9273539372821713, 0.03399132966962419, 0.03309689125699233, 0.07516870380715912, 0.3800268890908792, 0.2876861148914786, 0.8794529506804162, 0.07133614600713696, 0.03254996547684294, 0.026929289760516242, 0.35676223124976264, 0.46847679792658037, 0.5521474577421718, 0.06459592048414536, 0.06271340448809985, 0.36017052409621175, 0.4705456400733705, 0.5554582690225726, 0.4985340885748191, 0.10389500464596016, 0.04384911288194861, 0.487755624390976, 0.5188930583498056, 0.5113087075955445, 0.5482863331838965, 0.06568262490556342, 0.3303087109152396, 0.4762050332527927, 0.465946723

In [ ]:
print(min(y1a))
print(max(y1a))

0.002415212270018878
1.0


###Combining Data and Train Test Split

In [ ]:
#Combine lists into dataframe
dataframe = pd.DataFrame(
    {'pw': x1a,
     'vwl': x2a,
     'vbsl': x3a,
     'preread': x5a
    })

In [ ]:
#Train-Test 70%-30% split
x = dataframe[["pw","vwl","vbsl","preread"]].to_numpy()
y = np.array(y1a)
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

In [ ]:
x

array([[0.01      , 0.1470588 , 0.16666667, 0.03431788],
       [0.01      , 0.1470588 , 0.33333333, 0.04190577],
       [0.01      , 0.1470588 , 0.5       , 0.040792  ],
       ...,
       [0.01      , 0.1470588 , 1.        , 0.05514082],
       [0.01      , 0.17647056, 0.16666667, 0.07995579],
       [0.01      , 0.17647056, 0.33333333, 0.05964901]])

###Training/Testing Model

In [ ]:
print("Training MLPRegressor...")
tic = time()
est = make_pipeline(
    QuantileTransformer(),
    MLPRegressor(
        hidden_layer_sizes=(45, 23),
        learning_rate_init=0.03,
        early_stopping=True,
        random_state=0,
    ),
)
est.fit(X_train, y_train)
print(f"done in {time() - tic:.3f}s")
print(f"Test R2 score: {est.score(X_test, y_test):.5f}")

Training MLPRegressor...
done in 29.797s
Test R2 score: 0.96316


In [ ]:
#Mean Squared Error
predictions = est.predict(X_train)
mean_squared_error(y_train, predictions, squared=False)

0.062183079317664716

In [ ]:
mean_squared_error(y_train, predictions, squared=True)

0.0038667353534269813

#Various Subsets

In [ ]:
total_dataframe = pd.DataFrame(
    {'pw': x1a,
     'vwl': x2a,
     'vbsl': x3a,
     'preread': x5a,
     'postread': y1a
    })

###Postread Conductance ONLY Subset

In [ ]:
cond_subset = []

count = 0
for element in total_dataframe['postread']:
  if element >= 0.5:
    cond_subset.append(element)
    count += 1

print(count/(len(total_dataframe['postread'])))
# the above code tells us around 56% of the postread conductances are above the 0.5

0.557098388671875


In [ ]:
np.average(total_dataframe['postread'])

0.4754557273904655

In [ ]:
cond_df = total_dataframe[total_dataframe['postread'] >= 0.5]
cond_df

pw       vwl      vbsl   preread  postread
9      0.01  0.176471  0.666667  0.903011  0.910478
17     0.01  0.205882  1.000000  0.932109  0.927354
23     0.01  0.235294  1.000000  0.892019  0.879453
29     0.01  0.264706  1.000000  0.059732  0.552147
34     0.01  0.294118  0.833333  0.058380  0.555458
...     ...       ...       ...       ...       ...
32753  1.00  0.970588  1.000000  0.089709  0.852628
32756  1.00  1.000000  0.500000  0.042824  0.635402
32757  1.00  1.000000  0.666667  0.108055  0.750463
32758  1.00  1.000000  0.833333  0.028018  0.793074
32759  1.00  1.000000  1.000000  0.040988  0.811036

[18255 rows x 5 columns]

In [ ]:
x11 = cond_df[['pw']]
x22 = cond_df[['vwl']]
x33 = cond_df[['vbsl']]
x44 = cond_df[['preread']]
y11 = cond_df[['postread']]

In [ ]:
x1b = list(x11['pw'])
x2b = list(x22['vwl'])
x3b = list(x33['vbsl'])
x4b = list(x44['preread'])
y1b = list(y11['postread'])

In [ ]:
#Combine lists into dataframe
dataframe2 = pd.DataFrame(
    {'pw': x1b,
     'vwl': x2b,
     'vbsl': x3b,
     'preread': x4b
    })

In [ ]:
#Train-Test 70%-30% split
x = dataframe2[["pw","vwl","vbsl","preread"]].to_numpy()
y = np.array(y1b)
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

In [ ]:
x

array([[0.01      , 0.17647056, 0.66666667, 0.90301115],
       [0.01      , 0.20588232, 1.        , 0.93210911],
       [0.01      , 0.23529408, 1.        , 0.89201891],
       ...,
       [1.        , 0.99999984, 0.66666667, 0.10805486],
       [1.        , 0.99999984, 0.83333333, 0.02801783],
       [1.        , 0.99999984, 1.        , 0.04098764]])

In [ ]:
print("Training MLPRegressor...")
tic = time()
est = make_pipeline(
    QuantileTransformer(),
    MLPRegressor(
        hidden_layer_sizes=(45, 23),
        learning_rate_init=0.03,
        early_stopping=True,
        random_state=0,
    ),
)
est.fit(X_train, y_train)
print(f"done in {time() - tic:.3f}s")
print(f"Test R2 score: {est.score(X_test, y_test):.5f}")

Training MLPRegressor...
done in 3.891s
Test R2 score: 0.75968


In [ ]:
#Mean Squared Error
predictions = est.predict(X_train)
mean_squared_error(y_train, predictions, squared=False)

0.05273433611455297

In [ ]:
#relatively similar mean squared error to the entire dataset
mean_squared_error(y_train, predictions, squared=True)

0.0027809102054426457

###(Significant Change 50%) Preread - Postread Conductance Subset

In [ ]:
subtr_df = total_dataframe[np.abs(total_dataframe['preread'] - total_dataframe['postread']) >= 0.5]
subtr_df

pw       vwl      vbsl   preread  postread
46     0.01  0.352941  0.833333  0.052877  0.595374
47     0.01  0.352941  1.000000  0.055367  0.663543
51     0.01  0.382353  0.666667  0.036685  0.607948
52     0.01  0.382353  0.833333  0.062256  0.712036
56     0.01  0.411765  0.500000  0.032252  0.578200
...     ...       ...       ...       ...       ...
32753  1.00  0.970588  1.000000  0.089709  0.852628
32756  1.00  1.000000  0.500000  0.042824  0.635402
32757  1.00  1.000000  0.666667  0.108055  0.750463
32758  1.00  1.000000  0.833333  0.028018  0.793074
32759  1.00  1.000000  1.000000  0.040988  0.811036

[14302 rows x 5 columns]

In [ ]:
#44% of the data has a different of over 0.5 between preread and postread resistance
len(subtr_df['postread']) / len(total_dataframe['postread'])

0.43646240234375

In [ ]:
x111 = subtr_df[['pw']]
x222 = subtr_df[['vwl']]
x333 = subtr_df[['vbsl']]
x444 = subtr_df[['preread']]
y111 = subtr_df[['postread']]

In [ ]:
x1c = list(x111['pw'])
x2c = list(x222['vwl'])
x3c = list(x333['vbsl'])
x4c = list(x444['preread'])
y1c = list(y111['postread'])

In [ ]:
#Combine lists into dataframe
dataframe2 = pd.DataFrame(
    {'pw': x1c,
     'vwl': x2c,
     'vbsl': x3c,
     'preread': x4c
    })

In [ ]:
#Train-Test 70%-30% split
x = dataframe2[["pw","vwl","vbsl","preread"]].to_numpy()
y = np.array(y1c)
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

In [ ]:
x

array([[0.01      , 0.35294112, 0.83333333, 0.05287704],
       [0.01      , 0.35294112, 1.        , 0.05536726],
       [0.01      , 0.38235288, 0.66666667, 0.03668541],
       ...,
       [1.        , 0.99999984, 0.66666667, 0.10805486],
       [1.        , 0.99999984, 0.83333333, 0.02801783],
       [1.        , 0.99999984, 1.        , 0.04098764]])

In [ ]:
print("Training MLPRegressor...")
tic = time()
est = make_pipeline(
    QuantileTransformer(),
    MLPRegressor(
        hidden_layer_sizes=(45, 23),
        learning_rate_init=0.03,
        early_stopping=True,
        random_state=0,
    ),
)
est.fit(X_train, y_train)
print(f"done in {time() - tic:.3f}s")
print(f"Test R2 score: {est.score(X_test, y_test):.5f}")

Training MLPRegressor...
done in 2.082s
Test R2 score: 0.75433


In [ ]:
#Mean Squared Error
predictions = est.predict(X_train)
mean_squared_error(y_train, predictions, squared=False)

0.047751288794933525

In [ ]:
#Mean Squared Error
predictions = est.predict(X_test)
mean_squared_error(y_test, predictions, squared=False)

0.04738344428663443

In [ ]:
#relatively similar mean squared error to the entire dataset
mean_squared_error(y_test, predictions, squared=True)

0.0022451907924645885

###(Miniscule Change 5%) Preread - Postread Conductance Subset

In [ ]:
ten_df = total_dataframe[np.abs(total_dataframe['preread'] - total_dataframe['postread']) <= 0.05]
ten_df

pw       vwl      vbsl   preread  postread
0      0.01  0.147059  0.166667  0.034318  0.044375
1      0.01  0.147059  0.333333  0.041906  0.040857
2      0.01  0.147059  0.500000  0.040792  0.047866
3      0.01  0.147059  0.666667  0.055790  0.038148
4      0.01  0.147059  0.833333  0.068648  0.088728
...     ...       ...       ...       ...       ...
32763  0.01  0.147059  0.666667  0.047479  0.054263
32764  0.01  0.147059  0.833333  0.045670  0.045872
32765  0.01  0.147059  1.000000  0.055141  0.071448
32766  0.01  0.176471  0.166667  0.079956  0.066338
32767  0.01  0.176471  0.333333  0.059649  0.041649

[12424 rows x 5 columns]

In [ ]:
#62% of the data has a difference of over 0.05 between preread and postread resistance
#this is the data population where the pulse width likely actually affects the resistance
len(ten_df['postread']) / len(total_dataframe['postread'])

0.379150390625

In [ ]:
x1111 = ten_df[['pw']]
x2222 = ten_df[['vwl']]
x3333 = ten_df[['vbsl']]
x4444 = ten_df[['preread']]
y1111 = ten_df[['postread']]

In [ ]:
x1d = list(x1111['pw'])
x2d = list(x2222['vwl'])
x3d = list(x3333['vbsl'])
x4d = list(x4444['preread'])
y1d = list(y1111['postread'])

In [ ]:
#Combine lists into dataframe
dataframe2 = pd.DataFrame(
    {'pw': x1d,
     'vwl': x2d,
     'vbsl': x3d,
     'preread': x4d
    })

In [ ]:
#Train-Test 70%-30% split
x = dataframe2[["pw","vwl","vbsl","preread"]].to_numpy()
y = np.array(y1d)
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

In [ ]:
x

array([[0.01      , 0.1470588 , 0.16666667, 0.03431788],
       [0.01      , 0.1470588 , 0.33333333, 0.04190577],
       [0.01      , 0.1470588 , 0.5       , 0.040792  ],
       ...,
       [0.01      , 0.1470588 , 1.        , 0.05514082],
       [0.01      , 0.17647056, 0.16666667, 0.07995579],
       [0.01      , 0.17647056, 0.33333333, 0.05964901]])

In [ ]:
print("Training MLPRegressor...")
tic = time()
est = make_pipeline(
    QuantileTransformer(),
    MLPRegressor(
        hidden_layer_sizes=(45, 23),
        learning_rate_init=0.03,
        early_stopping=True,
        random_state=0,
    ),
)
est.fit(X_train, y_train)
print(f"done in {time() - tic:.3f}s")
print(f"Test R2 score: {est.score(X_test, y_test):.5f}")

Training MLPRegressor...
done in 3.619s
Test R2 score: 0.99420


In [ ]:
#Mean Squared Error
predictions = est.predict(X_train)
mean_squared_error(y_train, predictions, squared=False)

0.01972682854112548

In [ ]:
#Mean Squared Error
predictions = est.predict(X_test)
mean_squared_error(y_test, predictions, squared=False)

0.02001072250219552

In [ ]:
#relatively similar mean squared error to the entire dataset
mean_squared_error(y_test, predictions, squared=True)

0.00040042901505987414

#Data Visualizations

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
data

In [ ]:
pw_subset1 = data[np.bitwise_and(data.iloc[:,2]==0.5,data.iloc[:,3]==0.5)]
pw_subset1  